## 15. Réfléchir à un autre type de réseau afin de résoudre ce problème

**=> Réseau Antagoniste Génératif (GAN)**
Les GAN sont composés de deux réseaux : un générateur qui crée des échantillons à partir de bruit, et un discriminateur qui apprend à distinguer les échantillons générés de ceux réels. Dans le contexte de la musique, un GAN pourrait générer de nouvelles séquences de notes en modifiant le générateur pour produire des séquences MIDI plausibles.

- Architecture :

  * Le générateur prendrait une séquence de bruit et produirait une séquence de notes et de durées.
  * Le discriminateur prendrait une séquence (notes et durées) et apprendrait à distinguer les séquences réelles (provenant du dataset) des séquences générées.

- Avantages :

  * Capacité à capturer des motifs complexes grâce à l'interaction compétitive entre le générateur et le discriminateur.
  * Potentiel de produire des séquences réalistes même sans supervision stricte sur la structure musicale.

- Inconvénients :

  * La formation des GAN est notoirement instable, ce qui pourrait entraîner des difficultés à générer des séquences de haute qualité.
  * Complexité plus élevée pour ajuster le modèle à la polyphonie et aux variations de tempo.


## 16. Bonus 1 : implémenter le réseau décrit à la question précédente.

In [1]:
import os
import numpy as np
import pretty_midi
import tensorflow as tf
from tensorflow.keras.layers import Dense, LSTM, Reshape, Conv1D, Flatten
from tensorflow.keras.models import Sequential
import IPython.display as ipd
import soundfile as sf

# Configuration de base
sequence_size = 100  # Nombre de notes par séquence
vocab_size = 128  # Ajusté pour couvrir la gamme de notes
latent_dim = 100  # Dimension de l'espace latent pour le générateur

In [2]:
# 1. Chargement et préparation des fichiers MIDI
midi_dir = "./Jazz Midi"
midi_files = [os.path.join(midi_dir, f) for f in os.listdir(midi_dir) if f.endswith(".mid")]

def load_midi(file_path):
    """Charge un fichier MIDI et retourne des listes de notes et de durées."""
    try:
        midi_data = pretty_midi.PrettyMIDI(file_path)
        notes = []
        for instrument in midi_data.instruments:
            if not instrument.is_drum:
                for note in instrument.notes:
                    notes.append(note.pitch)
        return notes
    except Exception as e:
        print(f"Error loading {file_path}: {str(e)}")
        return []  # Retourne une liste vide si le fichier ne peut pas être chargé

# Chargement des données MIDI
notes_sequences = []
for file in midi_files:
    notes = load_midi(file)
    if notes:
        notes_sequences.append(notes)

/opt/anaconda3/lib/python3.11/site-packages/pretty_midi/pretty_midi.py:100: RuntimeWarning: Tempo, Key or Time signature change events found on non-zero tracks.  This is not a valid type 0 or type 1 MIDI file.  Tempo, Key or Time Signature may be wrong.
  warnings.warn(


Error loading ./Jazz Midi/Lakes.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/StTropez.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/LovinTouchinSqueezin.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/Moment.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/AnyWayYouWantIt.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/Destiny.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/JamaicanNights.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/AffairInSanMiguel.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/TheCloserIGetToYou.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/CurvesAhead.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/CantilopeIsland.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/ThePrincess.mid: data byte must be in range 0..127
Error loading ./Jazz Midi/NativeSonsOfADistantLand.mid: data 

In [3]:
# Vectorisation et segmentation en séquences de taille fixe
def create_sequences(data, sequence_length=sequence_size + 1):
    sequences = []
    for item in data:
        for i in range(0, len(item) - sequence_length, sequence_length):
            sequences.append(item[i:i + sequence_length])
    return sequences

# Transformation en séquences et ajustement du vocab_size
notes_sequences = create_sequences(notes_sequences)
notes_sequences = tf.convert_to_tensor(notes_sequences, dtype=tf.int32)

In [4]:
# Création des jeux d'entraînement pour le GAN
x_train = notes_sequences[:, :-1]
y_train = notes_sequences[:, 1:]

In [5]:
# 2. Modèles de générateur et de discriminateur
def build_generator(latent_dim, sequence_size, vocab_size):
    model = Sequential()
    # Calculate the right size for reshaping
    reshape_dim = sequence_size * 1  # target size for reshaping
    
    model.add(Dense(reshape_dim, input_dim=latent_dim, activation='relu'))
    model.add(Reshape((sequence_size, 1)))
    model.add(Conv1D(64, kernel_size=3, padding="same", activation="relu"))
    model.add(LSTM(128, return_sequences=True))
    model.add(Dense(vocab_size, activation="softmax"))
    return model

In [6]:
def build_discriminator(sequence_size, vocab_size):
    model = Sequential()
    model.add(Conv1D(64, kernel_size=3, padding="same", input_shape=(sequence_size, vocab_size)))
    model.add(LSTM(128, return_sequences=True))
    model.add(Flatten())
    model.add(Dense(1, activation="sigmoid"))
    return model

In [7]:
# # Update configuration
# sequence_size = 100
# vocab_size = 128
# latent_dim = 100

# generator = build_generator(latent_dim, sequence_size, vocab_size)
# discriminator = build_discriminator(sequence_size, vocab_size)
# discriminator.compile(optimizer="adam", loss="binary_crossentropy", metrics=["accuracy"])

# # Construction du GAN en combinant générateur et discriminateur
# discriminator.trainable = False
# gan_input = tf.keras.Input(shape=(latent_dim,))
# generated_notes = generator(gan_input)
# gan_output = discriminator(generated_notes)
# gan = tf.keras.Model(gan_input, gan_output)
# gan.compile(optimizer="adam", loss="binary_crossentropy")

# 1. First compile the discriminator separately
discriminator = build_discriminator(sequence_size, vocab_size)
discriminator.compile(optimizer="adam", loss="binary_crossentropy", metrics=["accuracy"])

# 2. Build the GAN
gan_input = tf.keras.Input(shape=(latent_dim,))
generator = build_generator(latent_dim, sequence_size, vocab_size)

# Generate notes using the generator
generated_notes = generator(gan_input)

# Only train generator weights in the combined model
discriminator.trainable = False  # Freeze discriminator weights when training generator
gan_output = discriminator(generated_notes)

# Create and compile GAN
gan = tf.keras.Model(gan_input, gan_output)
gan.compile(optimizer="adam", loss="binary_crossentropy")

/opt/anaconda3/lib/python3.11/site-packages/keras/src/layers/convolutional/base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)
/opt/anaconda3/lib/python3.11/site-packages/keras/src/layers/core/dense.py:87: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


In [8]:
# 3. Entraînement du GAN
# Training loop
epochs = 100
batch_size = 16

for epoch in range(epochs):
    # Generate noise for fake samples
    noise = np.random.normal(0, 1, (batch_size, latent_dim))
    generated_sequences = generator.predict(noise)
    
    # Sample real sequences
    idx = tf.random.uniform([batch_size], 0, x_train.shape[0], dtype=tf.int32)
    real_sequences = tf.gather(x_train, idx)
    real_sequences = tf.one_hot(real_sequences, vocab_size)
    
    # Train discriminator
    discriminator.trainable = True
    d_loss_real = discriminator.train_on_batch(real_sequences, np.ones((batch_size, 1)))
    d_loss_fake = discriminator.train_on_batch(generated_sequences, np.zeros((batch_size, 1)))
    
    # Train generator
    discriminator.trainable = False
    g_loss = gan.train_on_batch(noise, np.ones((batch_size, 1)))
    
    # Print progress
    if epoch % 1000 == 0:
        print(f"Epoch {epoch}, D Loss Real: {d_loss_real}, D Loss Fake: {d_loss_fake}, G Loss: {g_loss}")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 153ms/step
Epoch 0, D Loss Real: [array(0.70067924, dtype=float32), array(0.3125, dtype=float32)], D Loss Fake: [array(0.7082292, dtype=float32), array(0.15625, dtype=float32)], G Loss: [array(0.7082292, dtype=float32), array(0.7082292, dtype=float32), array(0.15625, dtype=float32)]
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step


In [9]:
# Sauvegarde du générateur
generator.save("03-gan_generator.h5")

Modèle de générateur sauvegardé.


In [10]:
# 4. Génération de nouveaux morceaux
def generate_music(generator, latent_dim, num_notes=100, output_path="generated_music.mid"):
    noise = np.random.normal(0, 1, (1, latent_dim))
    generated_sequence = generator.predict(noise)
    generated_notes = tf.argmax(generated_sequence, axis=-1).numpy().flatten()

    # Création du fichier MIDI
    midi_data = pretty_midi.PrettyMIDI()
    instrument = pretty_midi.Instrument(program=0)  # Piano par défaut
    current_time = 0  # Temps de démarrage pour la première note
    
    for pitch in generated_notes[:num_notes]:
        note = pretty_midi.Note(
            velocity=100,
            pitch=int(pitch),
            start=current_time,
            end=current_time + 0.5  # Durée fixe de 0.5 pour simplification
        )
        instrument.notes.append(note)
        current_time += 0.5
    
    midi_data.instruments.append(instrument)
    midi_data.write(output_path)
    print(f"Morceau généré et sauvegardé sous {output_path}")

# Générer un morceau
generate_music(generator, latent_dim, num_notes=100, output_path="generated_midis/03-generated_music.mid")


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 135ms/step
Morceau généré et sauvegardé sous generated_midis/03-generated_music.mid


In [11]:
output_file = "./generated_midis/03-gan.mid"
midi_data = pretty_midi.PrettyMIDI(output_file)

audio_file = "./generated_midis/03-gan.wav"
waveform = midi_data.synthesize()
sf.write(audio_file, waveform, samplerate=44100)

ipd.Audio(audio_file)